In [28]:
import pandas as pd
df=pd.read_csv('/content/sentiment_analysis.csv')
df

Year  Month  Day Time of Tweet  \
0    2018      8   18       morning   
1    2018      8   18          noon   
2    2017      8   18         night   
3    2022      6    8       morning   
4    2022      6    8          noon   
..    ...    ...  ...           ...   
494  2015     10   18         night   
495  2021      2   25       morning   
496  2022      5   30          noon   
497  2018      8   10         night   
498  2019      3   25       morning   

                                                  text sentiment     Platform  
0                What a great day!!! Looks like dream.  positive    Twitter    
1       I feel sorry, I miss you here in the sea beach  positive    Facebook   
2                                       Don't angry me  negative     Facebook  
3    We attend in the class just for listening teac...  negative    Facebook   
4                    Those who want to go, let them go  negative   Instagram   
..                                                 ...       ...          ...  
494  According to , a quarter of families under six...  negative     Twitter   
495      the plan to not spend money is not going well  negative   Instagram   
496    uploading all my bamboozle pictures of facebook   neutral    Facebook   
497   congratulations ! you guys finish a month ear...  positive     Twitter   
498   actually, I wish I was back in Tahoe.  I miss...  negative   Instagram   

[499 rows x 7 columns]

In [29]:
dataset = df[['text', 'sentiment']]

In [30]:
dataset['sentiment'] = dataset['sentiment'].replace({
    'negative': 0,
    'positive': 1,
    'neutral': 1
})
dataset.head()

/tmp/ipython-input-714633831.py:1: FutureWarning: Downcasting behavior in `replace` is deprecated and will be removed in a future version. To retain the old behavior, explicitly call `result.infer_objects(copy=False)`. To opt-in to the future behavior, set `pd.set_option('future.no_silent_downcasting', True)`
  dataset['sentiment'] = dataset['sentiment'].replace({
/tmp/ipython-input-714633831.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  dataset['sentiment'] = dataset['sentiment'].replace({


text  sentiment
0              What a great day!!! Looks like dream.          1
1     I feel sorry, I miss you here in the sea beach          1
2                                     Don't angry me          0
3  We attend in the class just for listening teac...          0
4                  Those who want to go, let them go          0

In [31]:
!pip install datasets transformers evaluate torch

In [32]:
from datasets import load_dataset
from transformers import AutoTokenizer, AutoModelForSequenceClassification, pipeline
import evaluate
import numpy as np

In [33]:
model_name = "distilbert-base-uncased-finetuned-sst-2-english"
tokenizer = AutoTokenizer.from_pretrained(model_name)
model = AutoModelForSequenceClassification.from_pretrained(model_name)

In [34]:
texts = df["text"].tolist()
true_labels = dataset["sentiment"].tolist()

In [35]:
sentiment_analyzer = pipeline("text-classification", model=model, tokenizer=tokenizer, device=0)


Device set to use cuda:0


In [36]:
predictions = sentiment_analyzer(texts)
predicted_labels = [1 if p["label"] == "POSITIVE" else 0 for p in predictions]

In [37]:
accuracy = evaluate.load("accuracy")
f1 = evaluate.load("f1")
precision = evaluate.load("precision")
recall = evaluate.load("recall")


In [38]:
acc_score = accuracy.compute(predictions=predicted_labels, references=true_labels)
f1_score = f1.compute(predictions=predicted_labels, references=true_labels)
prec_score = precision.compute(predictions=predicted_labels, references=true_labels)
rec_score = recall.compute(predictions=predicted_labels, references=true_labels)

print("\nHELM Evaluation Metrics")
print(f"Accuracy : {acc_score['accuracy']:.4f}")
print(f"Precision: {prec_score['precision']:.4f}")
print(f"Recall   : {rec_score['recall']:.4f}")
print(f"F1 Score : {f1_score['f1']:.4f}")


HELM Evaluation Metrics
Accuracy : 0.7114
Precision: 0.9333
Recall   : 0.6521
F1 Score : 0.7677


In [39]:
import torch
def compute_confidence(model, tokenizer, text):
    inputs = tokenizer(text, return_tensors="pt", truncation=True, padding=True)
    inputs = {k: v.to(model.device) for k, v in inputs.items()}
    outputs = model(**inputs)
    probs = torch.softmax(outputs.logits, dim=-1)
    return torch.max(probs).item()

confidences = [compute_confidence(model, tokenizer, t) for t in texts]
avg_confidence = np.mean(confidences)

print("\nApproximate Calibration Metric")
print(f"Average Model Confidence: {avg_confidence:.4f}")


Approximate Calibration Metric
Average Model Confidence: 0.9699


In [40]:

perturbed_texts = [t.replace("good", "excellent").replace("bad", "terrible") for t in texts]
perturbed_preds = sentiment_analyzer(perturbed_texts)
perturbed_labels = [1 if p["label"] == "POSITIVE" else 0 for p in perturbed_preds]

robustness_acc = accuracy.compute(predictions=perturbed_labels, references=true_labels)
print("\nRobustness Check")
print(f"Accuracy after small perturbations: {robustness_acc['accuracy']:.4f}")


Robustness Check
Accuracy after small perturbations: 0.7114
